# vdW Parameter Estimation for R32 and EmimTF2N
*Fitting classical vdW mixing parameters

Bridgette Befort and Alex Dowling, University of Notre Dame, 2022

## Load Libraries and Data File

In [1]:
ipopt_path = '/Users/bridgettebefort/src/CoinIpopt/build/bin/ipopt'
# ipopt_path = "/Users/adowling/src/CoinIpopt/build/bin/ipopt"

In [2]:
import pandas as pd
import numpy as np
import math
import matplotlib
import matplotlib.pyplot as plt

In [3]:
#load functions
from bip_regression_functions_vdw2param import *

In [4]:
#HFC32 critical T and P
Tc_HFC = 351.26 #[K]
Pc_HFC = 5.782 #[MPa]

In [5]:
#parameter bounds
bnds = ([-10.0,-10.0], [10.0,10.0])

## Mixtures

### R32/emimTF2N

#### Load Data

In [6]:
#Load Data
data_emimTF2N = pd.read_csv('r32_emimtf2n.csv')
data_emimTF2N

Set Measurement       T       P     x1
0  S1          m1  283.15  0.0102  0.014
1  S1          m2  283.15  0.1001  0.136
2  S1          m3  283.15  0.2503  0.306
3  S1          m4  283.15  0.3993  0.448
4  S1          m5  283.15  0.5493  0.570
5  S1          m6  283.15  0.7004  0.672
6  S1          m7  283.15  0.8494  0.786

#### Specify System Parameters

In [7]:
##BIP Dictionaries
#R32/emimTF2N
SP = SystemParameters(
    #Component Number
    ['HFC','IL'],

    #Critical temperature [K]
    {'HFC': 351.26, 'IL': 1000},

    # Critial pressure [MPa]
    {'HFC': 5.782, 'IL': 2.5},
     )

In [8]:
#Initialize fitted parameters
FP_init = FittedParameters(
    #k
    {('HFC','HFC'): 0,
    ('HFC','IL'): 0.9,     
    ('IL','HFC'): 1.0,
    ('IL','IL'): 0}
)

#### Model Exploration

In [9]:
#Calculate fugacity intermediates given initial fitted parameter guesses
Scipy_results = calculate_fugacity_detailed(FP_init, 
                                              SP,
                                              data_emimTF2N, 
                                              equilibrium=False) 
Scipy_results

{0: {'x1': 0.014,
  'a_pure': {'HFC': 0.6222761228949922, 'IL': 11.664438075},
  'a_mix': 11.343961024165413,
  'b_pure': {'HFC': 0.06313506658595641, 'IL': 0.4157},
  'b_mix': 0.4107640909322034,
  'alpha_l': -1.001779778909783,
  'beta_l': 0.020879097636697805,
  'gamma_l': -3.716017762909692e-05,
  'VL': 0.45342045107747464,
  'A_star_L': 0.020879097636697805,
  'B_star_L': 0.0017797789097831,
  'Z_compressibility_L': 0.001964602490594103,
  'ln_phi_L': 8.8660324553271,
  'phi_L_HFC': 7087.106706338179,
  'alpha_v': -1.0002735547299726,
  'beta_v': 0.0011453286818627958,
  'gamma_v': -3.133100782969556e-07,
  'VV': 230.5936503387363,
  'A_star_V': 0.0011453286818627958,
  'B_star_V': 0.00027355472997269136,
  'Z_compressibility_V': 0.9991275397793207,
  'ln_phi_V': -0.003976625442313421,
  'phi_V_HFC': 0.9960312708622913,
  'P': 0.0102},
 1: {'x1': 0.136,
  'a_pure': {'HFC': 0.6222761228949922, 'IL': 11.664438075},
  'a_mix': 8.750623449036658,
  'b_pure': {'HFC': 0.0631350665859564

#### Fit Model

In [10]:
#Fitted Params list
#theta = [kij,kji]

theta0 = [-0.1,1.0] #initial guess
#using inexact newton method version 2 with line search
fitted_theta = optimize.least_squares(regression_func, theta0, 
                                      method='trf',
                                      args=(data_emimTF2N['T'],data_emimTF2N['x1'],data_emimTF2N['P'],SP,2),
                                     bounds=bnds,
                                     verbose=1)
print("\nBest fit parameters:")
print(fitted_theta.x)

x0 = -6.907755278982137
x_1 = -6.908e+00 - 1.000e+00 * -9.913e-01 / -7.899e-03 = -1.324003e+02 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 9.000e-01 * -9.913e-01 / -7.899e-03 = -1.198510e+02 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 8.100e-01 * -9.913e-01 / -7.899e-03 = -1.085567e+02 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 7.290e-01 * -9.913e-01 / -7.899e-03 = -9.839178e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 6.561e-01 * -9.913e-01 / -7.899e-03 = -8.924338e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 5.905e-01 * -9.913e-01 / -7.899e-03 = -8.100982e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 5.314e-01 * -9.913e-01 / -7.899e-03 = -7.359961e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 4.783e-01 * -9.913e-01 / -7.899e-03 = -6.693043e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 4.305e-01 * -9.913e-01 / -7.899e-03 = -6.092816e+01 < lower bound of -6.908e+00
x_1 = -6.908e+00 - 3.874e-01 * -9.913e-01 / -7.899e-03 = -5.552612e+01 < lower bound 

AssertionError: 

#### Grid Search for Good Initial Parameters

In [11]:
test_params = np.linspace(-1,1,20) #initial parameters to search through
fitted_theta_results = np.zeros(len(test_params)*len(test_params)) #array to save results

count = 0
#loop through parameter combinations
for i in test_params:
    for j in test_params:
        #Fitted Params list
        #[kij,kji]

        theta0 = [i,j]
        
        print('Trying theta0:',theta0)
        
        try: #try with the initial guess
            fitted_theta = optimize.least_squares(regression_func, theta0, 
                                                  method='trf',
                                                  args=(data_emimTF2N['T'],data_emimTF2N['x1'],data_emimTF2N['P'],SP,2),
                                                 bounds=bnds,
                                                 verbose=0)
            print("\nBest fit parameters:")
            print(fitted_theta.x)
            fitted_theta_results[count] = fitted_theta.x #save results
        except: #if the initial guess doesn't work save nan as parameter values
            fitted_theta = np.nan
            fitted_theta_results[count] = np.nan
        count += 1

Trying theta0: [-1.0, -1.0]
x0 = -6.907755278982137
x_1 = -6.908e+00 - 1.000e+00 * -9.996e-01 / 3.893e-04 = 2.561089e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 9.000e-01 * -9.996e-01 / 3.893e-04 = 2.304290e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 8.100e-01 * -9.996e-01 / 3.893e-04 = 2.073170e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 7.290e-01 * -9.996e-01 / 3.893e-04 = 1.865162e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 6.561e-01 * -9.996e-01 / 3.893e-04 = 1.677955e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.905e-01 * -9.996e-01 / 3.893e-04 = 1.509469e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.314e-01 * -9.996e-01 / 3.893e-04 = 1.357831e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 4.783e-01 * -9.996e-01 / 3.893e-04 = 1.221357e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 4.305e-01 * -9.996e-01 / 3.893e-04 = 1.098531e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 3.874e-01 * -9.996e-01 / 3.893e-04 = 9.879869e+02 > upper bound o

x_2 = 3.812e+00 - 9.000e-01 * -2.388e-05 / 6.812e-06 = 6.967171e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 8.100e-01 * -2.388e-05 / 6.812e-06 = 6.651703e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 7.290e-01 * -2.388e-05 / 6.812e-06 = 6.367782e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 6.561e-01 * -2.388e-05 / 6.812e-06 = 6.112253e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 5.905e-01 * -2.388e-05 / 6.812e-06 = 5.882276e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 5.314e-01 * -2.388e-05 / 6.812e-06 = 5.675298e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 4.783e-01 * -2.388e-05 / 6.812e-06 = 5.489017e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 4.305e-01 * -2.388e-05 / 6.812e-06 = 5.321364e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 3.874e-01 * -2.388e-05 / 6.812e-06 = 5.170477e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 3.487e-01 * -2.388e-05 / 6.812e-06 = 5.034678e+00 > upper bound of 4.606e+00
x_2 = 3.812e+00 - 3.138e-01 * -2.388e-05 / 6.812e-

x_1 = -6.908e+00 - 7.290e-01 * -9.996e-01 / 3.893e-04 = 1.865160e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 6.561e-01 * -9.996e-01 / 3.893e-04 = 1.677953e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.905e-01 * -9.996e-01 / 3.893e-04 = 1.509467e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.314e-01 * -9.996e-01 / 3.893e-04 = 1.357830e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 4.783e-01 * -9.996e-01 / 3.893e-04 = 1.221356e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 4.305e-01 * -9.996e-01 / 3.893e-04 = 1.098530e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 3.874e-01 * -9.996e-01 / 3.893e-04 = 9.879859e+02 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 3.487e-01 * -9.996e-01 / 3.893e-04 = 8.884966e+02 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 3.138e-01 * -9.996e-01 / 3.893e-04 = 7.989561e+02 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 2.824e-01 * -9.996e-01 / 3.893e-04 = 7.183698e+02 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 2.542e-01 * -9.996e-0

x_2 = 3.812e+00 - 1.251e-06 * -2.388e-05 / 6.812e-06 = 3.812488e+00,  f(x_2) = -2.388e-05
x_2 = 3.812e+00 - 1.126e-06 * -2.388e-05 / 6.812e-06 = 3.812487e+00,  f(x_2) = -2.388e-05
x_2 = 3.812e+00 - 1.013e-06 * -2.388e-05 / 6.812e-06 = 3.812487e+00,  f(x_2) = -2.388e-05
Terminated. Line search failure with alpha < 1.0e-06.
Trying theta0: [-1.0, 0.894736842105263]
x0 = -6.907755278982137
x_1 = -6.908e+00 - 1.000e+00 * -9.996e-01 / 3.893e-04 = 2.561086e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 9.000e-01 * -9.996e-01 / 3.893e-04 = 2.304286e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 8.100e-01 * -9.996e-01 / 3.893e-04 = 2.073167e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 7.290e-01 * -9.996e-01 / 3.893e-04 = 1.865160e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 6.561e-01 * -9.996e-01 / 3.893e-04 = 1.677953e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.905e-01 * -9.996e-01 / 3.893e-04 = 1.509467e+03 > upper bound of 4.606e+00
x_1 = -6.908e+00 - 5.314e-01 * -9.9

x_2 = 3.827e+00 - 1.310e-03 * -2.378e-05 / 6.314e-06 = 3.832087e+00,  f(x_2) = -2.375e-05
x_2 = 3.827e+00 - 1.179e-03 * -2.378e-05 / 6.314e-06 = 3.831593e+00,  f(x_2) = -2.375e-05
x_2 = 3.827e+00 - 1.061e-03 * -2.378e-05 / 6.314e-06 = 3.831149e+00,  f(x_2) = -2.376e-05
x_2 = 3.827e+00 - 9.550e-04 * -2.378e-05 / 6.314e-06 = 3.830750e+00,  f(x_2) = -2.376e-05
x_2 = 3.827e+00 - 8.595e-04 * -2.378e-05 / 6.314e-06 = 3.830390e+00,  f(x_2) = -2.376e-05
x_2 = 3.827e+00 - 7.736e-04 * -2.378e-05 / 6.314e-06 = 3.830066e+00,  f(x_2) = -2.376e-05
x_2 = 3.827e+00 - 6.962e-04 * -2.378e-05 / 6.314e-06 = 3.829775e+00,  f(x_2) = -2.376e-05
x_2 = 3.827e+00 - 6.266e-04 * -2.378e-05 / 6.314e-06 = 3.829513e+00,  f(x_2) = -2.377e-05
x_2 = 3.827e+00 - 5.639e-04 * -2.378e-05 / 6.314e-06 = 3.829277e+00,  f(x_2) = -2.377e-05
x_2 = 3.827e+00 - 5.075e-04 * -2.378e-05 / 6.314e-06 = 3.829064e+00,  f(x_2) = -2.377e-05
x_2 = 3.827e+00 - 4.568e-04 * -2.378e-05 / 6.314e-06 = 3.828873e+00,  f(x_2) = -2.377e-05
x_2 = 3.82

...

x_1 = -6.908e+00 - 1.000e+00 * 9.606e+02 / -9.616e+02 = -5.908800e+00,  f(x_1) = 3.532e+02
x_2 = -5.909e+00 - 1.000e+00 * 3.532e+02 / -3.541e+02 = -4.911500e+00,  f(x_2) = 1.297e+02
x_3 = -4.912e+00 - 1.000e+00 * 1.297e+02 / -1.306e+02 = -3.918719e+00,  f(x_3) = 4.746e+01
x_4 = -3.919e+00 - 1.000e+00 * 4.746e+01 / -4.839e+01 = -2.938013e+00,  f(x_4) = 1.722e+01
x_5 = -2.938e+00 - 1.000e+00 * 1.722e+01 / -1.813e+01 = -1.988110e+00,  f(x_5) = 6.124e+00
x_6 = -1.988e+00 - 1.000e+00 * 6.124e+00 / -6.969e+00 = -1.109362e+00,  f(x_6) = 2.090e+00
x_7 = -1.109e+00 - 1.000e+00 * 2.090e+00 / -2.797e+00 = -3.620175e-01,  f(x_7) = 6.819e-01
x_8 = -3.620e-01 - 1.000e+00 * 6.819e-01 / -1.151e+00 = 2.302741e-01,  f(x_8) = 2.381e-01
x_9 = 2.303e-01 - 1.000e+00 * 2.381e-01 / -4.019e-01 = 8.226870e-01,  f(x_9) = 1.570e-01
x_9 = 2.303e-01 - 9.000e-01 * 2.381e-01 / -4.019e-01 = 7.634457e-01,  f(x_9) = 1.524e-01
x_9 = 2.303e-01 - 8.100e-01 * 2.381e-01 / -4.019e-01 = 7.101285e-01,  f(x_9) = 1.505e-01
x_9 = 

x_9 = 2.267e-01 - 6.752e-06 * 2.363e-01 / -4.024e-01 = 2.267344e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 6.076e-06 * 2.363e-01 / -4.024e-01 = 2.267340e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 5.469e-06 * 2.363e-01 / -4.024e-01 = 2.267336e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 4.922e-06 * 2.363e-01 / -4.024e-01 = 2.267333e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 4.430e-06 * 2.363e-01 / -4.024e-01 = 2.267330e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 3.987e-06 * 2.363e-01 / -4.024e-01 = 2.267327e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 3.588e-06 * 2.363e-01 / -4.024e-01 = 2.267325e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 3.229e-06 * 2.363e-01 / -4.024e-01 = 2.267323e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 2.906e-06 * 2.363e-01 / -4.024e-01 = 2.267321e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 2.616e-06 * 2.363e-01 / -4.024e-01 = 2.267319e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 2.354e-06 * 2.363e-01 / -4.024e-01 = 2.267318e-01,  f(x_9) = 2.363e-01
x_9 = 2.267e-01 - 2.1

x_10 = 2.581e+00 - 9.550e-04 * 4.887e-01 / -1.887e-01 = 2.583185e+00,  f(x_10) = 4.883e-01
x_10 = 2.581e+00 - 8.595e-04 * 4.887e-01 / -1.887e-01 = 2.582938e+00,  f(x_10) = 4.883e-01
x_10 = 2.581e+00 - 7.736e-04 * 4.887e-01 / -1.887e-01 = 2.582715e+00,  f(x_10) = 4.884e-01
x_10 = 2.581e+00 - 6.962e-04 * 4.887e-01 / -1.887e-01 = 2.582515e+00,  f(x_10) = 4.884e-01
x_10 = 2.581e+00 - 6.266e-04 * 4.887e-01 / -1.887e-01 = 2.582334e+00,  f(x_10) = 4.884e-01
x_10 = 2.581e+00 - 5.639e-04 * 4.887e-01 / -1.887e-01 = 2.582172e+00,  f(x_10) = 4.885e-01
x_10 = 2.581e+00 - 5.075e-04 * 4.887e-01 / -1.887e-01 = 2.582026e+00,  f(x_10) = 4.885e-01
x_10 = 2.581e+00 - 4.568e-04 * 4.887e-01 / -1.887e-01 = 2.581894e+00,  f(x_10) = 4.885e-01
x_10 = 2.581e+00 - 4.111e-04 * 4.887e-01 / -1.887e-01 = 2.581776e+00,  f(x_10) = 4.885e-01
x_10 = 2.581e+00 - 3.700e-04 * 4.887e-01 / -1.887e-01 = 2.581670e+00,  f(x_10) = 4.886e-01
x_10 = 2.581e+00 - 3.330e-04 * 4.887e-01 / -1.887e-01 = 2.581574e+00,  f(x_10) = 4.886e-01

x_10 = 2.580e+00 - 2.697e-04 * 4.863e-01 / -1.878e-01 = 2.580243e+00,  f(x_10) = 4.861e-01
x_10 = 2.580e+00 - 2.427e-04 * 4.863e-01 / -1.878e-01 = 2.580173e+00,  f(x_10) = 4.861e-01
x_10 = 2.580e+00 - 2.185e-04 * 4.863e-01 / -1.878e-01 = 2.580110e+00,  f(x_10) = 4.861e-01
x_10 = 2.580e+00 - 1.966e-04 * 4.863e-01 / -1.878e-01 = 2.580053e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.770e-04 * 4.863e-01 / -1.878e-01 = 2.580002e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.593e-04 * 4.863e-01 / -1.878e-01 = 2.579957e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.433e-04 * 4.863e-01 / -1.878e-01 = 2.579915e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.290e-04 * 4.863e-01 / -1.878e-01 = 2.579878e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.161e-04 * 4.863e-01 / -1.878e-01 = 2.579845e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 1.045e-04 * 4.863e-01 / -1.878e-01 = 2.579815e+00,  f(x_10) = 4.862e-01
x_10 = 2.580e+00 - 9.405e-05 * 4.863e-01 / -1.878e-01 = 2.579788e+00,  f(x_10) = 4.862e-01

x_10 = 2.578e+00 - 3.043e-03 * 4.834e-01 / -1.867e-01 = 2.586103e+00,  f(x_10) = 4.819e-01
x_10 = 2.578e+00 - 2.739e-03 * 4.834e-01 / -1.867e-01 = 2.585315e+00,  f(x_10) = 4.820e-01
x_10 = 2.578e+00 - 2.465e-03 * 4.834e-01 / -1.867e-01 = 2.584606e+00,  f(x_10) = 4.822e-01
x_10 = 2.578e+00 - 2.219e-03 * 4.834e-01 / -1.867e-01 = 2.583968e+00,  f(x_10) = 4.823e-01
x_10 = 2.578e+00 - 1.997e-03 * 4.834e-01 / -1.867e-01 = 2.583394e+00,  f(x_10) = 4.824e-01
x_10 = 2.578e+00 - 1.797e-03 * 4.834e-01 / -1.867e-01 = 2.582877e+00,  f(x_10) = 4.825e-01
x_10 = 2.578e+00 - 1.617e-03 * 4.834e-01 / -1.867e-01 = 2.582412e+00,  f(x_10) = 4.826e-01
x_10 = 2.578e+00 - 1.456e-03 * 4.834e-01 / -1.867e-01 = 2.581993e+00,  f(x_10) = 4.827e-01
x_10 = 2.578e+00 - 1.310e-03 * 4.834e-01 / -1.867e-01 = 2.581617e+00,  f(x_10) = 4.827e-01
x_10 = 2.578e+00 - 1.179e-03 * 4.834e-01 / -1.867e-01 = 2.581277e+00,  f(x_10) = 4.828e-01
x_10 = 2.578e+00 - 1.061e-03 * 4.834e-01 / -1.867e-01 = 2.580972e+00,  f(x_10) = 4.828e-01

In [ ]:
#print results of grid search
fitted_theta_results